In [9]:
import pandas as pd
import folium
from folium import Choropleth
from branca.colormap import LinearColormap

# URL of the Excel file on GitHub
url = 'Bailey_Python.xlsx'

# Read the Excel file from the GitHub URL
df = pd.read_excel(url)

# Drop rows with NaN values in the relevant columns
df = df.dropna(subset=['lat', 'lon', 'ppm'])

# Display the first few rows to ensure it's loaded correctly and NaNs are removed
print(df.head())

# Define categories for gasValue
def categorize(value):
    if value <= 100:
        return '0-100'
    elif 100 < value <= 500:
        return '100-500'
    else:
        return 'Above 500'

# Define a color palette
color_palette = {
    '0-100': '#FFD580',  # Light orange
    '100-500': 'orange',
    'Above 500': 'red'
}

# Create a base map centered around the average latitude and longitude
m = folium.Map(location=[df['lat'].mean(), df['lon'].mean()], zoom_start=10)

# Function to add CircleMarkers to the map based on category
def add_circle_markers(df, category):
    for _, row in df[df['category'] == category].iterrows():
        folium.CircleMarker(
            location=[row['lat'], row['lon']],
            radius=7,
            color=color_palette[category],
            fill=True,
            fill_color=color_palette[category],
            fill_opacity=1,
        ).add_to(m)

# Categorize the gas values
df['category'] = df['ppm'].apply(categorize)

# Add CircleMarkers for each category in the desired order
add_circle_markers(df, '0-100')
add_circle_markers(df, '100-500')
add_circle_markers(df, 'Above 500')

# Add a legend to the map (for visual reference) with opaque background
legend_html = """
    <div style="
        position: fixed; 
        bottom: 50px; left: 50px; width: 150px; height: 150px; 
        border:2px solid grey; background-color:white;
        opacity:1; z-index:9999; font-size:14px;
        ">
        <b>Gas Value Categories</b><br>
        <i style="background:#FFD580; width:24px; height:24px; display:inline-block;"></i> 0-100<br>
        <i style="background:orange; width:24px; height:24px; display:inline-block;"></i> 100-500<br>
        <i style="background:red; width:24px; height:24px; display:inline-block;"></i> Above 500
    </div>
"""
m.get_root().html.add_child(folium.Element(legend_html))

# Save the map to an HTML file
m.save('circle_map.html')

# Display the map (optional, only works in Jupyter Notebooks or IPython environments)
m


   ppm        lat         lon
0  7.4  49.111325 -121.928824
1  7.6  49.111326 -121.928827
2  6.4  49.111336 -121.928836
3  6.9  49.111362 -121.928843
4  5.9  49.111386 -121.928840
